# Tic Tac Toe: `Cube` and Game Logic

In today's lecture, we're going to implement `Cube` and `TTTcube`. We already have a good sense of what it should do after our last class, but let’s look at the details.

We're also going to implement the game logic by: keeping track of players ("X" and "O" alternate), having player choose row + column, using methods in `Cube` and `TTTcube` and `TTTboard` to check for win after each move.

## Abstraction

We have already seen a glimpse of what `Cube` and `TTTcube` needs to do
In fact it has to support this functionality for `TTTboard`!

In [ ]:
class Cube(): 
    def __init__(self, letter):
        """ Initializes Cube with given letter text.
        Parameters
        ----------
        letter : str
            letter to assign as cube value
        """
        self._letter = letter

    def set_letter(self, letter):
        """ Changes cube's current letter value to letter. 
        Parameters
        ----------
        letter : str
            Value for cube to show
        """
        self._letter = letter
        
    def get_letter(self):
        """ Accessor returns cube's current letter value.
        Returns
        -------
        str
            Value of cube currently showing
        """
        return self._letter
    def __str__(self):
        """ Simple string representation of a Cube."""
        return self._letter

## TTTcube Class

`TTTCube` can use most of `Cube`...but needs a little special initialization.

In [ ]:
class TTTcube(Cube):
    """ Represents a Tic-Tac-Toe game cube."""
    def __init__(self):
        """ TTT Cube initial values are '-'."""
        super().__init__('-')
    
    # override Cube set_letter to be enforce TTT rules
    def set_letter(self, letter) :
        """
        If letter is an 'X', 'O', or '-' (empty),
        update the cube's letter
        """
        if letter in "XO-":
            self._letter = letter

### Testing TTTcube

It’s always a good idea to test our class and methods in isolation:

In [ ]:
letter = TTTcube()
print(letter)

In [ ]:
letter.set_letter("X")
print(letter)

In [ ]:
letter2 = TTTcube()
letter2.set_letter("O")
print(letter2)

In [ ]:
letter3 = TTTcube()
letter3.set_letter("B")
print(letter3)

We'll need `Board` and `TTTboard` to implement the game logic:

In [ ]:
################################
##           BOARD            ##
##           Day 1            ##
################################

class Board:
    """ Represents a Game Board for a letter-based grid game. """
    
    __slots__ = [ '_rows', '_cols', '_grid' ]

    def __init__(self, rows, cols):  
        """ Initializes board with row and columns, 
        and initial cubes. 
        
        Parameters
        ----------
        rows : int
            number of rows for this grid-based cube game
        cols : int
            number of cols for this grid-based cube game
        grid : list of list
            a rows x cols sized grid to store game pieces
            """
        self._rows = rows
        self._cols = cols

        # initialize grid to be rows x cols in size, with `None` as the placeholder value
        self._grid = [ [None for _ in range(self._cols)] for _ in range(self._rows)]

    def get_rows(self):
        """ Accessor to return number of rows of this board. 

        Returns
        -------
        int
            How many rows this game board has.
        """
        return self._rows
    
    def get_cols(self):
        """ Accessor to return number of cols of this board. 

        Returns
        -------
        int
            How many columns this game board has.
        """
        return self._cols
    
    def set_cube(self, row, col, new_cube):
        """ Changes cube at given location to new_cube.

        Parameters
        ----------
        row : int
            row location of cube to set
        col : int
            column location of cube to set
        new_cube: Cube
            Cube object to set at this location
            """
        self._grid[row][col] = new_cube

    def get_cube(self, row, col):
        """ Accessor returns Cube at given location. 

        Parameters
        ----------
        row : int
            row location of cube to get
        col : int
            column location of cube to get
        Returns
        -------
        Cube
            Cube object located at this location
        """
        return self._grid[row][col]
    
    def __str__(self):
        """ String representation of a Board. """
        result = ""

        for row in self._grid:
            for cube in row:
                # Basic is to display string of each cube, separated by a space
                result = result + str(cube) + ' '
            result = result + '\n'

        return result

We can now extend the `Board` class with features that are specific to tic-tac-toe (and even replace select `Board` methods with tic-tac-toe-specific implementations that enforce some of the tic-tac-toe rules). We get all of the benefits of the existing `Board` code, and only need to change/add what is necessary for tic-tac-toe.

In [ ]:
class TTTboard(Board):
    """ Represents a Tic-Tac-Toe Board for gameplay. """
    def __init__(self):  
        """ Creates initial TTT board with starter letters. """
        super().__init__(3, 3)

        for r in range(self._rows):
            for c in range(self._cols):
                self._grid[r][c] = TTTcube()

    def reset(self):
        """ Helper method to reset the TTTboard"""
        for row in self._grid:
            for cube in row:
                cube.set_letter("-")

Now that we've built a custom TTT board class, we can start to develop the game logic. Let's first write a class that represent the game logic, starting with the task of "checking for wins".

In [ ]:

class TTTgame :
    __slots__ = [ '_tttboard' ]

    def __init__(self, tttboard) :
        self._tttboard = tttboard
        self._tttboard.reset()
    
    def _check_win_rows(self, letter):
        """ Check rows for a win (3 in a row) 
        
        Parameters
        ----------
        letter : str
            letter to check for wins
        Returns
        -------
        bool
            True if 3-in-a-row along row
        """
        rows = self._tttboard._rows
        cols = self._tttboard._cols

        for row in range(rows):
            count = 0
            for col in range(cols):
                ttt_letter = self._tttboard._grid[row][col]

                # check how many times letter appears
                if ttt_letter.get_letter() == letter:
                    count += 1
        
            # a win if the entire row was letter
            if count == cols:
                return True
        
        # no winning row found
        return False
    
    def _check_win_cols(self, letter):
        """ Check columns for a win (3 in a row) 
        
        Parameters
        ----------
        letter : str
            letter to check for wins
        Returns
        -------
        bool
            True if 3-in-a-row along columns
        """
        rows = self._tttboard._rows
        cols = self._tttboard._cols

        for col in range(cols):
            count = 0
            for row in range(rows):
                ttt_letter = self._tttboard._grid[row][col]

                # check how many times letter appears
                if ttt_letter.get_letter() == letter:
                    count += 1
            if count == rows:
                return True
        
        # no winning col found
        return False

    def _check_win_diagonals(self, letter):
        """ Check diagonals for a win (3 in a row) 
        
        Parameters
        ----------
        letter : str
            letter to check for wins
        Returns
        -------
        bool
            True if 3-in-a-row along diagonals
        """
        # counts for primary and secondary diagonal
        count_primary = 0
        count_second = 0

        rows = self._tttboard._rows
        cols = self._tttboard._cols
        for row in range(rows):
            for col in range(cols):
                ttt_letter = self._tttboard._grid[row][col]

                # update count for primary diagonal
                if row == col and ttt_letter.get_letter() == letter:
                    count_primary += 1

                # update count for secondary diagonal
                if row+col == rows-1 and ttt_letter.get_letter() == letter:
                    count_second += 1
        
        # return true if either win
        return count_primary == rows or count_second == rows
    

    
    def check_for_win(self, letter):
        """ Returns True if 3-in-a-row win found. 
        
        Parameters
        ----------
        letter : str
            letter to check for wins
        Returns
        -------
        bool
            True if 3-in-a-row win for letter/player
        """
        row_win = self._check_win_rows(letter)
        col_win = self._check_win_cols(letter)
        diag_win = self._check_win_diagonals(letter)

        return row_win or col_win or diag_win

We should always test as we go! This would go in a `if __name__ == "__main__"` code block.

In [ ]:
board = TTTboard()
game = TTTgame(board)

# no one has made any moves, so we shouldn't have a winner yet...
game_over = game.check_for_win("X") or game.check_for_win("O")
print(game_over)

# although, we could check if "-" won :)
print(game.check_for_win("-"))

## Game Logic

Let’s create a TTT flowchart to help us think through the state of the game at various stages:

* Let’s think about the “common” case: a valid move in the middle of the game
* Now let’s consider the case of a win, draw, or invalid move
* Now’s let suppose a player chooses reset 
* Now’s let suppose a player chooses exit
* Finally, let’s handle choosing not to exit


### Translating our Logic to Code

Let’s think about a `TTTgame` method called `play_text_game()`: What information do we need?
 * a board (already an attribute)
 * a player (what type should player be?)
 * the number of turns played so far (to detect draws easily?)

We'll need a few if-elif-else checks to handle the grid/reset/exit check. Let’s start with that logic and fill the rest in later.
 * We can handle the “exit” option first (since it’s the easiest), then test that it works before moving to reset.

Then let’s write a method to ask the a player to specify their move.
 * they must provide a *valid* row & column
    * start by converting to `int`...then check that it is a valid location

In [ ]:
class TTTgame :
    # add players, current player, and number of turns to existing attributes
    __slots__ = [ '_tttboard', '_players', '_player', '_turns' ]

    def __init__(self, tttboard) :
        self._tttboard = tttboard
        self._players = ("X", "O")
        self.reset()
    
    # reset method re-initializes an empty game within an existing TTTgame
    def reset(self):
        self._player = 0
        self._turns = 0
        self._tttboard.reset()
        
    
    def _check_win_rows(self, letter):
        """ Check rows for a win (3 in a row) 
        
        Parameters
        ----------
        letter : str
            letter to check for wins
        Returns
        -------
        bool
            True if 3-in-a-row along row
        """
        rows = self._tttboard._rows
        cols = self._tttboard._cols

        for row in range(rows):
            count = 0
            for col in range(cols):
                ttt_letter = self._tttboard._grid[row][col]

                # check how many times letter appears
                if ttt_letter.get_letter() == letter:
                    count += 1
        
            # a win if the entire row was letter
            if count == cols:
                return True
        
        # no winning row found
        return False
    
    def _check_win_cols(self, letter):
        """ Check columns for a win (3 in a row) 
        
        Parameters
        ----------
        letter : str
            letter to check for wins
        Returns
        -------
        bool
            True if 3-in-a-row along columns
        """
        rows = self._tttboard._rows
        cols = self._tttboard._cols

        for col in range(cols):
            count = 0
            for row in range(rows):
                ttt_letter = self._tttboard._grid[row][col]

                # check how many times letter appears
                if ttt_letter.get_letter() == letter:
                    count += 1
            if count == rows:
                return True
        
        # no winning col found
        return False

    def _check_win_diagonals(self, letter):
        """ Check diagonals for a win (3 in a row) 
        
        Parameters
        ----------
        letter : str
            letter to check for wins
        Returns
        -------
        bool
            True if 3-in-a-row along diagonals
        """
        # counts for primary and secondary diagonal
        count_primary = 0
        count_second = 0

        rows = self._tttboard._rows
        cols = self._tttboard._cols
        for row in range(rows):
            for col in range(cols):
                ttt_letter = self._tttboard._grid[row][col]

                # update count for primary diagonal
                if row == col and ttt_letter.get_letter() == letter:
                    count_primary += 1

                # update count for secondary diagonal
                if row+col == rows-1 and ttt_letter.get_letter() == letter:
                    count_second += 1
        
        # return true if either win
        return count_primary == rows or count_second == rows
    
    def check_for_win(self, letter):
        """ Returns True if 3-in-a-row win found. 
        
        Parameters
        ----------
        letter : str
            letter to check for wins
        Returns
        -------
        bool
            True if 3-in-a-row win for letter/player
        """
        row_win = self._check_win_rows(letter)
        col_win = self._check_win_cols(letter)
        diag_win = self._check_win_diagonals(letter)

        return row_win or col_win or diag_win
    
    # Our interactive gameplay logic!
    def play_text_game(self):
        """ Game logic/display for text-based TTT. """

        keep_going = True

        # While we haven't run out of cells
        # ...and we don't have a winner...play!
        while keep_going:
            player = self._players[self._player]

            print("It's {}'s turn! (Turn {})".format(player, self._turns))
            print(self._tttboard)

            # Ask player for row/col
            row = input("Input row: ")
            col = input("Input col: ")

            # Reset or quit before converting row/col to int
            if row == 'r' or col == 'r': # reset
                self.reset()
            
            elif row == 'q' or col == 'q': # exit
                keep_going = False

            # Is it valid?
            elif row.isdigit() and col.isdigit():
                row = int(row)
                col = int(col)
                if(row < self._tttboard.get_rows() and col < self._tttboard.get_cols()) and self._tttboard.get_cube(row, col).get_letter() == "-":

                    self._turns += 1 # a successful move was made

                    self._tttboard.get_cube(row, col).set_letter(player) # Place letter

                    game_over = False # assume game continues until proven otherwise

                    if self.check_for_win(player): # Winner?
                        print()
                        print(self._tttboard)
                        print(player, "wins!!")
                        game_over = True
                    elif (self._turns) == 3*3: # Draw?
                        print()
                        print(self._tttboard)
                        print("DRAW!")
                        game_over = True

                    print()

                    if game_over: # draw or win, ask to reset?
                        reset = input("Reset? (y)")
                        if reset == 'y':
                            self.reset()
                        else:
                            keep_going = False

                    # Switch player every other turn
                    self._player = self._turns % 2

                else:
                    print("Row/Col choice out of grid, try again!")
            else: # Invalid move
                print("Invalid selection, try again!")

Now we can test our game. Again, this would go inside an `if __name__ == "__main__"` code block.

In [ ]:
board = TTTboard()
game = TTTgame(board)
game.play_text_game()

### Reflecting on `play_text_game`

Are there more opportunities for inheritance in the implementation of the game logic? What common features can we imagine both tic-tac-toe and Boggle need?

* Turn-taking
* Collecting user choice of row & column
* Check it's valid
* Digit, and in bounds of our cube grid
* Checking for reset or quit
* Actually resetting & quitting!

'Might come up again while building a graphical user interface (GUI) for Tic-Tac-Toe...

## Basic strategy

* Board & Cube: start general, don’t think about game specific details
* TTTboard: extend generic board with TTT specific features
   * Inherit everything, update attributes/methods as needed
* TTTcube: isolate functionality of a single TTTcube on board
   * Think about what features are necessary/helpful in other classes 
* TTTgame
   * what game logic can we encode as methods? making moves, checking wins, accepting input...
   * play_text_game(): think through logic conceptually before writing any code
   * Translate logic into code carefully, testing along the way

## Next Time

Adding the **Graphical User Interface** layer to our text-based game!